In [1]:
import numpy as np
from easyscience.Datasets.xarray import xr
from easyscience.Objects.Base import Parameter, BaseObj
from easyscience.Fitting.Fitting import Fitter

In [ ]:
try:
    import hvplot.xarray
except:
    import sys
    !{sys.executable} -m pip install hvplot
    import hvplot.xarray

# 1D Data

In [13]:
# Create a dataset
d = xr.Dataset()

# Create a coreObject
b = BaseObj('line',
            m=Parameter('m', 1),
            c=Parameter('c', 1))

# Create a fit function to use with b
def fit_fun(x, *args, **kwargs):
    return b.c.raw_value + b.m.raw_value * x


# Create and initialize the fitter
f = Fitter()
f.initialize(b, fit_fun)

# Generate some `fake` data to fit to
nx = 1E3
x_min = 0
x_max = 100

x = np.linspace(x_min, x_max, num=int(nx))
y = 2*x - 1 + 5*(np.random.random(size=x.shape) - 0.5)

# Add the data to the dataset
d.easyscience.add_coordinate('x', x)
d.easyscience.add_variable('y', ['x'], y, auto_sigma=False)

# Perform the fit
f_res = d['y'].easyscience.fit(f)

In [14]:
# Plot the results
d['fit'] = f_res.y_calc.unstack()
d.hvplot(y=['y','fit'])

:NdOverlay   [Variable]
   :Curve   [x]   (value)

# 2D Data

In [16]:
# Variables to be used for `fake` data generation
nx = 5E2
x_min = 0
x_max = 3

sin_offest = - 0.35
cos_offset = 0.14
s_off_start_point = 0
c_off_start_point = 0

In [18]:
d = xr.Dataset()

# Generate some `x`, `y`, `z` data
x = np.linspace(x_min, x_max, num=int(nx))
y = x + 1
z = np.sin(2*np.pi*(x + sin_offest)).reshape((-1, 1))* np.cos(2*np.pi*(x + cos_offset)).reshape((1, -1)) + \
    2*(0.5 - np.random.random(size=(int(nx), int(nx))))

# Add it to the dataset
d.easyscience.add_coordinate('x', x)
d.easyscience.add_coordinate('y', y)
d.easyscience.add_variable('z', ['x', 'y'], z)


# easyscience Object
b = BaseObj('line',
            s_off=Parameter('s_off', s_off_start_point),
            c_off=Parameter('c_off', c_off_start_point))

# The fitting function
def fit_fun(x, *args, **kwargs):
    return np.sin(2*np.pi*(x[:, 0] + b.s_off.raw_value)) * np.cos(2*np.pi*(x[:, 1] + b.c_off.raw_value))

In [7]:
d

<xarray.Dataset>
Dimensions:  (x: 500, y: 500)
Coordinates:
  * x        (x) float64 0.0 0.006012 0.01202 0.01804 ... 2.982 2.988 2.994 3.0
  * y        (y) float64 1.0 1.006 1.012 1.018 1.024 ... 3.982 3.988 3.994 4.0
Data variables:
    z        (x, y) float64 0.3882 -1.286 -0.8712 ... -0.3584 -1.213 -0.3778
Attributes:
    name:         
    description:  
    url:          
    units:        {'x': <Unit('dimensionless')>, 'y': <Unit('dimensionless')>...

In [19]:
d['z'].hvplot()

:Image   [y,x]   (z)

In [20]:

f = Fitter()
f.initialize(b, fit_fun)
minimizer = f.current_engine

f_res = d['z'].easyscience.fit(f)
d[f'computed_{minimizer}'] = f_res.y_calc.unstack()
d[f'dz_{minimizer}'] = d['z'] - d[f'computed_{minimizer}']


d[f'computed_{minimizer}'].hvplot()

:Image   [y,x]   (computed_<class 'easyCore.Fitting.lmfit.lmfit'>)

In [10]:
d[f'dz_{minimizer}'].hvplot()

:Image   [y,x]   (dz_<class 'easyCore.Fitting.lmfit.lmfit'>)

In [11]:
x_array = f_res.x.unstack()
x_array[0]

<xarray.DataArray 'axes_broadcast' (x: 500, y: 500)>
array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.00601202, 0.00601202, 0.00601202, ..., 0.00601202, 0.00601202,
        0.00601202],
       [0.01202405, 0.01202405, 0.01202405, ..., 0.01202405, 0.01202405,
        0.01202405],
       ...,
       [2.98797595, 2.98797595, 2.98797595, ..., 2.98797595, 2.98797595,
        2.98797595],
       [2.99398798, 2.99398798, 2.99398798, ..., 2.99398798, 2.99398798,
        2.99398798],
       [3.        , 3.        , 3.        , ..., 3.        , 3.        ,
        3.        ]])
Coordinates:
  * x        (x) float64 0.0 0.006012 0.01202 0.01804 ... 2.982 2.988 2.994 3.0
  * y        (y) float64 1.0 1.006 1.012 1.018 1.024 ... 3.982 3.988 3.994 4.0